In [1]:
import os

import numpy as np
from qonnx.core.modelwrapper import ModelWrapper

import finn.core.onnx_exec as oxe

from qonnx.custom_op.registry import getCustomOp

from finn.util.basic import pynq_part_map
import pandas as pd

from finn.transformation.fpgadataflow.prepare_ip import PrepareIP
from finn.transformation.fpgadataflow.hlssynth_ip import HLSSynthIP
from finn.transformation.fpgadataflow.create_stitched_ip import CreateStitchedIP

from finn.transformation.fpgadataflow.set_exec_mode import SetExecMode
from finn.transformation.fpgadataflow.prepare_rtlsim import PrepareRTLSim

from finn.transformation.fpgadataflow.annotate_cycles import AnnotateCycles
from finn.analysis.fpgadataflow.dataflow_performance import dataflow_performance
from finn.util.basic import (
    get_rtlsim_trace_depth,
    pyverilate_get_liveness_threshold_cycles,
)

# Setup Folders and Model Filenames

In [2]:
experiment_folder = ('../qonnx_to_finn_driver'
                     + '/experiments_pynq-z1'
                     + '/1295_pynq-z1__200FPS__workspace__AIMET_Balanced__BIPOLAR__w4W2a4__full_build'
                     + '/output_full_build')
model_folder = experiment_folder + '/intermediate_models'

qonnx_to_finn = model_folder + '/step_qonnx_to_finn.onnx'
stitched_ip = model_folder + '/step_create_stitched_ip.onnx'
parent_model = model_folder + '/dataflow_parent.onnx'

stitched_rtlsim_filename = "./rtl_sim/stitched_rtlsim.onnx"

# Function to prepare model for RTLSim: FIFOs impl_style from "vivado" to "rtl"

In [3]:
def prepare_for_stitched_ip_rtlsim(verify_model, fpga_part, target_clk_ns):
    need_restitch = False
    # switch impl_style=vivado components to rtl
    # StreamingFIFO must have impl_style=rtl
    for fifo_layer in verify_model.get_nodes_by_op_type("StreamingFIFO_rtl"):
        inst = getCustomOp(fifo_layer)
        if inst.get_nodeattr("impl_style") != "rtl":
            inst.set_nodeattr("impl_style", "rtl")
            inst.set_nodeattr("code_gen_dir_ipgen", "")
            inst.set_nodeattr("ipgen_path", "")
            need_restitch = True
    # if we've made alterations to the model, need to do some re-prep
    if need_restitch:
        print("Need to regen/re-stitch some IP for STITCHED_IP_RTLSIM")
        verify_model = verify_model.transform(
            PrepareIP(fpga_part, target_clk_ns)
        )
        verify_model = verify_model.transform(HLSSynthIP())
        verify_model = verify_model.transform(
            CreateStitchedIP(
                fpga_part,
                target_clk_ns,
                vitis=False,
            )
        )
  
    # set top-level prop for stitched-ip rtlsim and launch
    verify_model.set_metadata_prop("exec_mode", "rtlsim")
    # TODO make configurable
    # verify_model.set_metadata_prop("rtlsim_trace", "trace.vcd")
    return verify_model

# PYNQ Boards Available

In [4]:
fpga_df = pd.DataFrame(pynq_part_map.items(), columns=['Board', 'FPGA Part'])
fpga_df

Board              FPGA Part
0     Ultra96    xczu3eg-sbva484-1-e
1  Ultra96-V2    xczu3eg-sbva484-1-i
2     Pynq-Z1        xc7z020clg400-1
3     Pynq-Z2        xc7z020clg400-1
4      ZCU102   xczu9eg-ffvb1156-2-e
5      ZCU104   xczu7ev-ffvc1156-2-e
6      ZCU111  xczu28dr-ffvg1517-2-e
7    RFSoC2x2  xczu28dr-ffvg1517-2-e
8    RFSoC4x2  xczu48dr-ffvg1517-2-e
9   KV260_SOM    xck26-sfvc784-2LV-c

In [5]:
# change this if you have a different PYNQ board, see list above
pynq_board = "Pynq-Z1"
fpga_part = pynq_part_map[pynq_board]
print(fpga_part)

xc7z020clg400-1


In [6]:
synth_clk_period_ns = 10.0

# Create New Stitched IP with impl_style = "rtl"

Only needed the first time, to create the new stitched IP. Once it is created, this step can be skipped

In [7]:
child_model = ModelWrapper(stitched_ip)

child_model = prepare_for_stitched_ip_rtlsim(child_model, fpga_part, synth_clk_period_ns)

child_model = child_model.transform(PrepareRTLSim())
child_model.save(stitched_rtlsim_filename)

%Warning-WIDTH: /home/gmoreno/workspace/code_gen_ipgen_StreamingFIFO_rtl_79_36ah4s5_/Q_srl.v:122:54: Operator EQ expects 32 or 2 bits on the LHS, but LHS's VARREF 'addr_' generates 1 bits.
                                                                                                   : ... In instance StreamingFIFO_rtl_79.impl
  122 |    assign addr_full_ = (state_==state_more) && (addr_==depth-2);
      |                                                      ^~
                ... For warning description see https://verilator.org/warn/WIDTH?v=4.224
                ... Use "/* verilator lint_off WIDTH */" and lint_on around source to disable this message.
%Warning-WIDTH: /home/gmoreno/workspace/code_gen_ipgen_StreamingFIFO_rtl_79_36ah4s5_/Q_srl.v:179:10: Operator ASSIGN expects 1 bits on the Assign RHS, but Assign RHS's SUB generates 32 or 2 bits.
                                                                                                   : ... In instance StreamingFIFO_rtl_79.

make: Entering directory '/home/gmoreno/workspace/pyverilator_StreamingFIFO_rtl_78_my65z6j7'
ccache g++  -I.  -MMD -I/usr/local/share/verilator/include -I/usr/local/share/verilator/include/vltstd -DVM_COVERAGE=0 -DVM_SC=0 -DVM_TRACE=1 -DVM_TRACE_FST=0 -DVM_TRACE_VCD=1 -faligned-new -fcf-protection=none -Wno-bool-operation -Wno-sign-compare -Wno-uninitialized -Wno-unused-but-set-variable -Wno-unused-parameter -Wno-unused-variable -Wno-shadow     -fPIC --std=c++11  -std=gnu++17 -Os -c -o pyverilator_wrapper.o /home/gmoreno/workspace/pyverilator_StreamingFIFO_rtl_78_my65z6j7/pyverilator_wrapper.cpp
ccache g++  -I.  -MMD -I/usr/local/share/verilator/include -I/usr/local/share/verilator/include/vltstd -DVM_COVERAGE=0 -DVM_SC=0 -DVM_TRACE=1 -DVM_TRACE_FST=0 -DVM_TRACE_VCD=1 -faligned-new -fcf-protection=none -Wno-bool-operation -Wno-sign-compare -Wno-uninitialized -Wno-unused-but-set-variable -Wno-unused-parameter -Wno-unused-variable -Wno-shadow     -fPIC --std=c++11  -std=gnu++17 -Os -c -o

%Warning-WIDTH: /home/gmoreno/workspace/code_gen_ipgen_StreamingFIFO_rtl_77_er5xnp8a/Q_srl.v:122:54: Operator EQ expects 32 or 2 bits on the LHS, but LHS's VARREF 'addr_' generates 1 bits.
                                                                                                   : ... In instance StreamingFIFO_rtl_77.impl
  122 |    assign addr_full_ = (state_==state_more) && (addr_==depth-2);
      |                                                      ^~
                ... For warning description see https://verilator.org/warn/WIDTH?v=4.224
                ... Use "/* verilator lint_off WIDTH */" and lint_on around source to disable this message.
%Warning-WIDTH: /home/gmoreno/workspace/code_gen_ipgen_StreamingFIFO_rtl_77_er5xnp8a/Q_srl.v:179:10: Operator ASSIGN expects 1 bits on the Assign RHS, but Assign RHS's SUB generates 32 or 2 bits.
                                                                                                   : ... In instance StreamingFIFO_rtl_77.

make: Entering directory '/home/gmoreno/workspace/pyverilator_StreamingFIFO_rtl_77_iluy8hf6'
ccache g++  -I.  -MMD -I/usr/local/share/verilator/include -I/usr/local/share/verilator/include/vltstd -DVM_COVERAGE=0 -DVM_SC=0 -DVM_TRACE=1 -DVM_TRACE_FST=0 -DVM_TRACE_VCD=1 -faligned-new -fcf-protection=none -Wno-bool-operation -Wno-sign-compare -Wno-uninitialized -Wno-unused-but-set-variable -Wno-unused-parameter -Wno-unused-variable -Wno-shadow     -fPIC --std=c++11  -std=gnu++17 -Os -c -o pyverilator_wrapper.o /home/gmoreno/workspace/pyverilator_StreamingFIFO_rtl_77_iluy8hf6/pyverilator_wrapper.cpp
ccache g++  -I.  -MMD -I/usr/local/share/verilator/include -I/usr/local/share/verilator/include/vltstd -DVM_COVERAGE=0 -DVM_SC=0 -DVM_TRACE=1 -DVM_TRACE_FST=0 -DVM_TRACE_VCD=1 -faligned-new -fcf-protection=none -Wno-bool-operation -Wno-sign-compare -Wno-uninitialized -Wno-unused-but-set-variable -Wno-unused-parameter -Wno-unused-variable -Wno-shadow     -fPIC --std=c++11  -std=gnu++17 -Os -c -o

%Warning-WIDTH: /home/gmoreno/workspace/code_gen_ipgen_StreamingFIFO_rtl_75_o_f25p3u/Q_srl.v:122:54: Operator EQ expects 32 or 2 bits on the LHS, but LHS's VARREF 'addr_' generates 1 bits.
                                                                                                   : ... In instance StreamingFIFO_rtl_75.impl
  122 |    assign addr_full_ = (state_==state_more) && (addr_==depth-2);
      |                                                      ^~
                ... For warning description see https://verilator.org/warn/WIDTH?v=4.224
                ... Use "/* verilator lint_off WIDTH */" and lint_on around source to disable this message.
%Warning-WIDTH: /home/gmoreno/workspace/code_gen_ipgen_StreamingFIFO_rtl_75_o_f25p3u/Q_srl.v:179:10: Operator ASSIGN expects 1 bits on the Assign RHS, but Assign RHS's SUB generates 32 or 2 bits.
                                                                                                   : ... In instance StreamingFIFO_rtl_75.

...

make: Entering directory '/home/gmoreno/workspace/pyverilator_StreamingFIFO_rtl_2_ul6l3al2'
ccache g++  -I.  -MMD -I/usr/local/share/verilator/include -I/usr/local/share/verilator/include/vltstd -DVM_COVERAGE=0 -DVM_SC=0 -DVM_TRACE=1 -DVM_TRACE_FST=0 -DVM_TRACE_VCD=1 -faligned-new -fcf-protection=none -Wno-bool-operation -Wno-sign-compare -Wno-uninitialized -Wno-unused-but-set-variable -Wno-unused-parameter -Wno-unused-variable -Wno-shadow     -fPIC --std=c++11  -std=gnu++17 -Os -c -o pyverilator_wrapper.o /home/gmoreno/workspace/pyverilator_StreamingFIFO_rtl_2_ul6l3al2/pyverilator_wrapper.cpp
ccache g++  -I.  -MMD -I/usr/local/share/verilator/include -I/usr/local/share/verilator/include/vltstd -DVM_COVERAGE=0 -DVM_SC=0 -DVM_TRACE=1 -DVM_TRACE_FST=0 -DVM_TRACE_VCD=1 -faligned-new -fcf-protection=none -Wno-bool-operation -Wno-sign-compare -Wno-uninitialized -Wno-unused-but-set-variable -Wno-unused-parameter -Wno-unused-variable -Wno-shadow     -fPIC --std=c++11  -std=gnu++17 -Os -c -o v

%Warning-WIDTH: /home/gmoreno/workspace/code_gen_ipgen_Thresholding_rtl_0_jbid1fxr/thresholding.sv:132:55: Operator ADD expects 32 bits on the LHS, but LHS's VARREF 'DEEP_PIPELINE' generates 1 bits.
                                                                                                         : ... In instance Thresholding_rtl_0_axi_wrapper.core.impl
  132 |  localparam int unsigned  MAX_PENDING = (DEEP_PIPELINE+1)*N + 3;
      |                                                       ^
                ... For warning description see https://verilator.org/warn/WIDTH?v=4.224
                ... Use "/* verilator lint_off WIDTH */" and lint_on around source to disable this message.
%Warning-WIDTH: /home/gmoreno/workspace/code_gen_ipgen_Thresholding_rtl_0_jbid1fxr/thresholding.sv:220:25: Logical operator LOGAND expects 1 bit on the LHS, but LHS's VARREF 'DEPTH_TRIGGER_URAM' generates 32 bits.
                                                                                         

make: Entering directory '/home/gmoreno/workspace/pyverilator_StreamingDataWidthConverter_rtl_0_hdmehla0'
ccache g++  -I.  -MMD -I/usr/local/share/verilator/include -I/usr/local/share/verilator/include/vltstd -DVM_COVERAGE=0 -DVM_SC=0 -DVM_TRACE=1 -DVM_TRACE_FST=0 -DVM_TRACE_VCD=1 -faligned-new -fcf-protection=none -Wno-bool-operation -Wno-sign-compare -Wno-uninitialized -Wno-unused-but-set-variable -Wno-unused-parameter -Wno-unused-variable -Wno-shadow     -fPIC --std=c++11  -std=gnu++17 -Os -c -o pyverilator_wrapper.o /home/gmoreno/workspace/pyverilator_StreamingDataWidthConverter_rtl_0_hdmehla0/pyverilator_wrapper.cpp
ccache g++  -I.  -MMD -I/usr/local/share/verilator/include -I/usr/local/share/verilator/include/vltstd -DVM_COVERAGE=0 -DVM_SC=0 -DVM_TRACE=1 -DVM_TRACE_FST=0 -DVM_TRACE_VCD=1 -faligned-new -fcf-protection=none -Wno-bool-operation -Wno-sign-compare -Wno-uninitialized -Wno-unused-but-set-variable -Wno-unused-parameter -Wno-unused-variable -Wno-shadow     -fPIC --std=c++

%Warning-WIDTH: /home/gmoreno/workspace/code_gen_ipgen_StreamingFIFO_rtl_0_2m2629sf/Q_srl.v:122:54: Operator EQ expects 32 or 2 bits on the LHS, but LHS's VARREF 'addr_' generates 1 bits.
                                                                                                  : ... In instance StreamingFIFO_rtl_0.impl
  122 |    assign addr_full_ = (state_==state_more) && (addr_==depth-2);
      |                                                      ^~
                ... For warning description see https://verilator.org/warn/WIDTH?v=4.224
                ... Use "/* verilator lint_off WIDTH */" and lint_on around source to disable this message.
%Warning-WIDTH: /home/gmoreno/workspace/code_gen_ipgen_StreamingFIFO_rtl_0_2m2629sf/Q_srl.v:179:10: Operator ASSIGN expects 1 bits on the Assign RHS, but Assign RHS's SUB generates 32 or 2 bits.
                                                                                                  : ... In instance StreamingFIFO_rtl_0.impl
 

make: Entering directory '/home/gmoreno/workspace/pyverilator_StreamingFIFO_rtl_1_dxzsgzuk'
ccache g++  -I.  -MMD -I/usr/local/share/verilator/include -I/usr/local/share/verilator/include/vltstd -DVM_COVERAGE=0 -DVM_SC=0 -DVM_TRACE=1 -DVM_TRACE_FST=0 -DVM_TRACE_VCD=1 -faligned-new -fcf-protection=none -Wno-bool-operation -Wno-sign-compare -Wno-uninitialized -Wno-unused-but-set-variable -Wno-unused-parameter -Wno-unused-variable -Wno-shadow     -fPIC --std=c++11  -std=gnu++17 -Os -c -o pyverilator_wrapper.o /home/gmoreno/workspace/pyverilator_StreamingFIFO_rtl_1_dxzsgzuk/pyverilator_wrapper.cpp
ccache g++  -I.  -MMD -I/usr/local/share/verilator/include -I/usr/local/share/verilator/include/vltstd -DVM_COVERAGE=0 -DVM_SC=0 -DVM_TRACE=1 -DVM_TRACE_FST=0 -DVM_TRACE_VCD=1 -faligned-new -fcf-protection=none -Wno-bool-operation -Wno-sign-compare -Wno-uninitialized -Wno-unused-but-set-variable -Wno-unused-parameter -Wno-unused-variable -Wno-shadow     -fPIC --std=c++11  -std=gnu++17 -Os -c -o v

# Load Parent Model and link Partition (Child) to Stitched IP for RTLSim

In [8]:
# parent model
model_for_rtlsim = ModelWrapper(parent_model)
# reference child model
sdp_node = getCustomOp(model_for_rtlsim.graph.node[1])
sdp_node.set_nodeattr("model", stitched_rtlsim_filename)

# LIVENESS_THRESHOLD: adjust it to model Max Cycles -> Critical Path

In [9]:
stiched_rtlsim_model = ModelWrapper(stitched_rtlsim_filename)
stiched_rtlsim_model = stiched_rtlsim_model.transform(AnnotateCycles())
estimate_network_performance = stiched_rtlsim_model.analysis(dataflow_performance)
prev_liveness = pyverilate_get_liveness_threshold_cycles()

In [10]:
print(f'Previous LIVENESS_THRESHOLD = {prev_liveness}')
print(f'Estimated performance of Stuched_RTLSim\n{estimate_network_performance}')

Previous LIVENESS_THRESHOLD = 10000
Estimated performance of Stuched_RTLSim
{'critical_path_cycles': 12407016, 'max_cycles': 471744, 'max_cycles_node_name': 'MVAU_hls_3'}


In [11]:
os.environ["LIVENESS_THRESHOLD"] = str(
    int(estimate_network_performance["critical_path_cycles"])
)
#os.environ["LIVENESS_THRESHOLD"] = str(prev_liveness)

In [12]:
print(os.environ["LIVENESS_THRESHOLD"])

12407016


# Eval with DFire MINI

In [13]:
# DS_FOLDER = '../../datasets/dfire_mini/'

DS_FOLDER = '../../datasets/dfire_mini/4ex/'

#### Needed for DatasetMINI
# DS_FOLDER += 'test/'
# DS_FOLDER += 'train/'

DS_IMGS = DS_FOLDER + 'images/'
DS_LABELS = DS_FOLDER + 'labels/'

In [14]:
IMGS_LIST = sorted([DS_IMGS + img_file for img_file in os.listdir(DS_IMGS)])

In [16]:
print(f'Number of test samples: {len(IMGS_LIST)}')

Number of test samples: 4


In [22]:
import my_metrics as metrics

### Eval QONNX TO FINN model

In [23]:
qonnx_to_finn_model = ModelWrapper(qonnx_to_finn)

In [24]:
qonnx_to_finn_metrics = metrics.eval_quant_onnx(
    imgs_list = IMGS_LIST,
    labels_dir = DS_LABELS,
    model_wrapped = qonnx_to_finn_model,
    bipolar=True,
    divide_255=False) # Preprocess included

Number of test samples: 4



Testing:  25%|████████████████████████████████████▎                                                                                                            | 1/4 [00:06<00:20,  6.85s/it]

yhat before binarization: [ 1. -1.]
yhat after binarization: [1. 0.]
Image file: ../../datasets/dfire_mini/4ex/images/PublicDataset00856.jpg: 
	label [1. 0.]
	pred [1. 0.]


Testing:  50%|████████████████████████████████████████████████████████████████████████▌                                                                        | 2/4 [00:13<00:13,  6.83s/it]

yhat before binarization: [-1. -1.]
yhat after binarization: [0. 0.]
Image file: ../../datasets/dfire_mini/4ex/images/WEB02490.jpg: 
	label [0. 0.]
	pred [0. 0.]


Testing:  75%|████████████████████████████████████████████████████████████████████████████████████████████████████████████▊                                    | 3/4 [00:20<00:06,  6.85s/it]

yhat before binarization: [1. 1.]
yhat after binarization: [1. 1.]
Image file: ../../datasets/dfire_mini/4ex/images/WEB04682.jpg: 
	label [1. 1.]
	pred [1. 1.]


Testing: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:27<00:00,  6.85s/it]

yhat before binarization: [-1.  1.]
yhat after binarization: [0. 1.]
Image file: ../../datasets/dfire_mini/4ex/images/WEB10100.jpg: 
	label [0. 0.]
	pred [0. 1.]
Smoke -> TP: 2.0, FP: 0.0, TN: 2.0, FN: 0.0
Fire  -> TP: 1.0, FP: 1.0, TN: 2.0, FN: 0.0


### Eval Stitched IP model

In [25]:
stitched_metrics = metrics.eval_quant_onnx(
    imgs_list = IMGS_LIST,
    labels_dir = DS_LABELS,
    model_wrapped = model_for_rtlsim,
    bipolar=True,
    divide_255=False) # Preprocess included

Number of test samples: 4



Testing:   0%|                                                                                                                                                         | 0/4 [00:00<?, ?it/s]%Warning-MODDUP: /home/gmoreno/workspace/vivado_stitch_proj_ltq7zf1p/finn_design_wrapper.v:2891:8: Duplicate declaration of module: 'thresholding'
 2891 | module thresholding #(
      |        ^~~~~~~~~~~~
                 /home/gmoreno/workspace/vivado_stitch_proj_ltq7zf1p/finn_design_wrapper.v:1220:8: ... Location of original declaration
 1220 | module thresholding #(
      |        ^~~~~~~~~~~~
                 ... For warning description see https://verilator.org/warn/MODDUP?v=4.224
                 ... Use "/* verilator lint_off MODDUP */" and lint_on around source to disable this message.
%Warning-MODDUP: /home/gmoreno/workspace/vivado_stitch_proj_ltq7zf1p/finn_design_wrapper.v:7351:8: Duplicate declaration of module: 'thresholding'
 7351 | module thresholding #(
      |        ^~~~~~~~~~~~
   

make: Entering directory '/home/gmoreno/workspace/pyverilator_ipstitched_9zpqx_j4'
ccache g++  -I.  -MMD -I/usr/local/share/verilator/include -I/usr/local/share/verilator/include/vltstd -DVM_COVERAGE=0 -DVM_SC=0 -DVM_TRACE=1 -DVM_TRACE_FST=0 -DVM_TRACE_VCD=1 -faligned-new -fcf-protection=none -Wno-bool-operation -Wno-sign-compare -Wno-uninitialized -Wno-unused-but-set-variable -Wno-unused-parameter -Wno-unused-variable -Wno-shadow     -fPIC --std=c++11  -std=gnu++17 -Os -c -o pyverilator_wrapper.o /home/gmoreno/workspace/pyverilator_ipstitched_9zpqx_j4/pyverilator_wrapper.cpp
ccache g++  -I.  -MMD -I/usr/local/share/verilator/include -I/usr/local/share/verilator/include/vltstd -DVM_COVERAGE=0 -DVM_SC=0 -DVM_TRACE=1 -DVM_TRACE_FST=0 -DVM_TRACE_VCD=1 -faligned-new -fcf-protection=none -Wno-bool-operation -Wno-sign-compare -Wno-uninitialized -Wno-unused-but-set-variable -Wno-unused-parameter -Wno-unused-variable -Wno-shadow     -fPIC --std=c++11  -std=gnu++17 -Os -c -o verilated.o /usr/lo

Testing:  25%|████████████████████████████████████▎                                                                                                            | 1/4 [01:19<03:57, 79.07s/it]

yhat before binarization: [1. 0.]
yhat after binarization: [1. 0.]
Image file: ../../datasets/dfire_mini/4ex/images/PublicDataset00856.jpg: 
	label [1. 0.]
	pred [1. 0.]


...

yhat before binarization: [1. 1.]
yhat after binarization: [1. 1.]
Image file: ../../datasets/dfire_mini/4ex/images/WEB04682.jpg: 
	label [1. 1.]
	pred [1. 1.]


%Warning-MODDUP: /home/gmoreno/workspace/vivado_stitch_proj_ltq7zf1p/finn_design_wrapper.v:2891:8: Duplicate declaration of module: 'thresholding'
 2891 | module thresholding #(
      |        ^~~~~~~~~~~~
                 /home/gmoreno/workspace/vivado_stitch_proj_ltq7zf1p/finn_design_wrapper.v:1220:8: ... Location of original declaration
 1220 | module thresholding #(
      |        ^~~~~~~~~~~~
                 ... For warning description see https://verilator.org/warn/MODDUP?v=4.224
                 ... Use "/* verilator lint_off MODDUP */" and lint_on around source to disable this message.
%Warning-MODDUP: /home/gmoreno/workspace/vivado_stitch_proj_ltq7zf1p/finn_design_wrapper.v:7351:8: Duplicate declaration of module: 'thresholding'
 7351 | module thresholding #(
      |        ^~~~~~~~~~~~
                 /home/gmoreno/workspace/vivado_stitch_proj_ltq7zf1p/finn_design_wrapper.v:1220:8: ... Location of original declaration
 1220 | module thresholding #(
      |        ^~~~~~~~~~

make: Entering directory '/home/gmoreno/workspace/pyverilator_ipstitched_qbf174bj'
ccache g++  -I.  -MMD -I/usr/local/share/verilator/include -I/usr/local/share/verilator/include/vltstd -DVM_COVERAGE=0 -DVM_SC=0 -DVM_TRACE=1 -DVM_TRACE_FST=0 -DVM_TRACE_VCD=1 -faligned-new -fcf-protection=none -Wno-bool-operation -Wno-sign-compare -Wno-uninitialized -Wno-unused-but-set-variable -Wno-unused-parameter -Wno-unused-variable -Wno-shadow     -fPIC --std=c++11  -std=gnu++17 -Os -c -o pyverilator_wrapper.o /home/gmoreno/workspace/pyverilator_ipstitched_qbf174bj/pyverilator_wrapper.cpp
ccache g++  -I.  -MMD -I/usr/local/share/verilator/include -I/usr/local/share/verilator/include/vltstd -DVM_COVERAGE=0 -DVM_SC=0 -DVM_TRACE=1 -DVM_TRACE_FST=0 -DVM_TRACE_VCD=1 -faligned-new -fcf-protection=none -Wno-bool-operation -Wno-sign-compare -Wno-uninitialized -Wno-unused-but-set-variable -Wno-unused-parameter -Wno-unused-variable -Wno-shadow     -fPIC --std=c++11  -std=gnu++17 -Os -c -o verilated.o /usr/lo

Testing: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 4/4 [04:08<00:00, 62.17s/it]

yhat before binarization: [0. 1.]
yhat after binarization: [0. 1.]
Image file: ../../datasets/dfire_mini/4ex/images/WEB10100.jpg: 
	label [0. 0.]
	pred [0. 1.]
Smoke -> TP: 2.0, FP: 0.0, TN: 2.0, FN: 0.0
Fire  -> TP: 1.0, FP: 1.0, TN: 2.0, FN: 0.0


# Print Results

In [26]:
qonnx_to_finn_df = pd.DataFrame(qonnx_to_finn_metrics)
qonnx_to_finn_df

Smoke    Fire    Mean
Accuracy     1.0  0.7500  0.8750
Precision    1.0  0.5000  0.7500
Recall       1.0  1.0000  1.0000
F1           1.0  0.6667  0.8334

In [27]:
stitched_df = pd.DataFrame(stitched_metrics)
stitched_df

Smoke    Fire    Mean
Accuracy     1.0  0.7500  0.8750
Precision    1.0  0.5000  0.7500
Recall       1.0  1.0000  1.0000
F1           1.0  0.6667  0.8334